In [403]:
%load_ext autoreload
%autoreload 2
%matplotlib inline
%config InlineBackend.figure_format = 'retina'
import networkx as nx
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import warnings
warnings.filterwarnings('ignore')

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## LOAD DATA

In [404]:
year = 2015

***One Function***

In [405]:
def load_data():

    # load passenger data
    pass_air_data = pd.read_csv('../00_data/passengers.csv',)

    # remove rows with 'SPB', 'SSB', 'AIK', 'PCA'
    pass_air_data = pass_air_data[
        ~pass_air_data['ORIGIN'].isin(['SPB', 'SSB', 'AIK', 'PCA'])]
    
    # remove rows with 'SPB', 'SSB', 'AIK', 'PCA'
    pass_air_data = pass_air_data[
        ~pass_air_data['DEST'].isin(['SPB', 'SSB', 'AIK', 'PCA'])]

    # create passenger graph
    passenger_graph = nx.from_pandas_edgelist(
        pass_air_data, source='ORIGIN',
        target='DEST', edge_key='YEAR',
        edge_attr=['PASSENGERS', 'UNIQUE_CARRIER_NAME'],
        create_using=nx.MultiDiGraph())
    
    return passenger_graph

***Two Function***

In [406]:
# Loadin the GPS coordinates of all the airports
def load_airports_GPS_data(pass_network):

    lat_long = pd.read_csv(
            "../00_data/GlobalAirportDatabase.txt", delimiter=":", header=None
        )
    lat_long.columns = [
        "CODE4",
        "CODE3",
        "CITY",
        "PROVINCE",
        "COUNTRY",
        "UNKNOWN1",
        "UNKNOWN2",
        "UNKNOWN3",
        "UNKNOWN4",
        "UNKNOWN5",
        "UNKNOWN6",
        "UNKNOWN7",
        "UNKNOWN8",
        "UNKNOWN9",
        "LATITUDE",
        "LONGITUDE"
    ]

    # filter to lat long in the continental US
    us_airports = lat_long.query("LATITUDE > 20 and LATITUDE < 50 and LONGITUDE > -130 and LONGITUDE < -60")
    
    return us_airports

***Three Function***

In [407]:
def year_network(G, year):
    """ Extract edges for a particular year from
        a MultiGraph. The edge is also populated with
        two attributes, weight and weight_inv where
        weight is the number of passengers and
        weight_inv the inverse of it.
    """
    year_network = nx.DiGraph()
    for edge in G.edges:
        source, target, edge_year = edge
        if edge_year == year:
            attr = G[source][target][edge_year]
            year_network.add_edge(
                source, target,
                weight=attr['PASSENGERS'],
                weight_inv=1/(attr['PASSENGERS']
                if attr['PASSENGERS'] != 0.0 else 1),
                airlines=attr['UNIQUE_CARRIER_NAME'])
    return year_network

***Four Function***

In [408]:
def clean_network(pass_network, airport_network):
    """ Remove nodes with no edges
        and remove self loops
    """

    wanted_nodes = list(pass_network.nodes())
    us_airports = airport_network.query("CODE3 in @wanted_nodes").drop_duplicates(subset=["CODE3"]).set_index("CODE3")
    

    
    return us_airports


In [409]:
# master function
def get_networks(year):
    """ Get the passenger network and the airport network
        for a particular year
    """
    passenger_graph = load_data()
    airport_network = load_airports_GPS_data(passenger_graph)
    year_network_data = year_network(passenger_graph, year)
    airport_network = clean_network(year_network_data, airport_network)
    return year_network_data, airport_network

In [410]:
pass_data, air_data = get_networks(year)

In [411]:
# Annotate graph with latitude and longitude
no_gps = []
for n, d in pass_data.nodes(data=True):
    try:
        pass_data.nodes[n]["longitude"] = air_data.loc[n, "LONGITUDE"] 
        pass_data.nodes[n]["latitude"] = air_data.loc[n, "LATITUDE"]
        pass_data.nodes[n]["degree"] = pass_data.degree(n)
        
    # Some of the nodes are not represented 
    except KeyError:
        no_gps.append(n)

# Get subgraph of nodes that do have GPS coords
has_gps = set(pass_data.nodes()).difference(no_gps)
g = pass_data.subgraph(has_gps)

Let's first plot only the nodes, i.e airports. Places like Guam, US Virgin Islands are also included in this dataset as they are treated as domestic airports in this dataset.

In [412]:
# add betweenness centrality to nodes
bc = nx.betweenness_centrality(pass_data, weight='weight_inv')
nx.set_node_attributes(pass_data, bc, 'betweenness_centrality')

# convert the graph to a dataframe
edge_df = nx.to_pandas_edgelist(pass_data)



In [413]:
# make an colormap for the nodes
node_cmap = plt.cm.Reds_r


In [414]:
# plot the nodes as a folium plot
import folium
import matplotlib as mpl

# Create a map
m = folium.Map(
    location=[39.8283, -98.5795],
    tiles='CartoDB dark_matter',
    zoom_start=4,
    min_lat=20,
    max_lat=50,
    min_lon=-130,
    max_lon=-60,
    max_bounds=True,
    max_zoom=6,
    min_zoom=4,
)

# add edges to the map from pass_data
for index, row in edge_df.iterrows():

    # if the source and target are in the air_data dataframe
    if row["source"] in air_data.index and row["target"] in air_data.index:

        # get the source and target coordinates
        source = air_data.loc[row["source"]]
        target = air_data.loc[row["target"]]

        # create a line from the source to the target
        line = folium.PolyLine(
            locations=[[source["LATITUDE"], source["LONGITUDE"]], [target["LATITUDE"], target["LONGITUDE"]]],
            color="firebrick",
            weight=0.2,
            opacity=0.1,
        ).add_to(m)

# # reverse sort air_data by betweenness centrality
# air_data = air_data.sort_values(by="betweenness_centrality", ascending=True)


# add nodes to the map from air_data and color by betweenness centrality
for index, row in air_data.iterrows():

    # if the node is in the pass_data
    if row.name in pass_data.nodes():

        # get the node coordinates
        node = pass_data.nodes[row.name]

        # node_color = node["betweenness_centrality"]

        node_color = node["betweenness_centrality"]

        OldMin = 0
        OldMax = 1
        NewMin = 0
        NewMax = 255

        OldValue = node_color

        OldRange = (OldMax - OldMin)  
        NewRange = (NewMax - NewMin)  
        node_color = int((((OldValue - OldMin) * NewRange) / OldRange) + NewMin)

        node_size = (node_color + 1) / 256 * 20

        node_color = node_cmap(node_color)

        # convert the node color to hex
        node_color = mpl.colors.rgb2hex(node_color)

        # create a circle marker from the node
        # and color by betweenness centrality
        # and add it to the map
        folium.CircleMarker(
            location=[node["latitude"], node["longitude"]],
            radius=node_size,
            color=node_color,
            fill=True,
            fill_color=node_color,
            fill_opacity=1,
            tooltip=row["CITY"],
        ).add_to(m)    
    
m